In [12]:
import pandas as pd
import numpy as np
from sklearn.model_selection import cross_val_score
from sklearn.model_selection import train_test_split

# Data exploration and preprocessnig

In [13]:
data_frame = pd.read_csv("data/train.csv")

In [14]:
data_frame.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1458644 entries, 0 to 1458643
Data columns (total 11 columns):
id                    1458644 non-null object
vendor_id             1458644 non-null int64
pickup_datetime       1458644 non-null object
dropoff_datetime      1458644 non-null object
passenger_count       1458644 non-null int64
pickup_longitude      1458644 non-null float64
pickup_latitude       1458644 non-null float64
dropoff_longitude     1458644 non-null float64
dropoff_latitude      1458644 non-null float64
store_and_fwd_flag    1458644 non-null object
trip_duration         1458644 non-null int64
dtypes: float64(4), int64(3), object(4)
memory usage: 122.4+ MB


Define two functions for later use.


In [15]:
print("from: long {} lat {}".format((data_frame.dropoff_latitude.min()), (data_frame.dropoff_longitude.min()))  )
print("to: long {} lat {}".format(max(data_frame.dropoff_latitude), max(data_frame.dropoff_longitude))  )

from: long 32.1811408996582 lat -121.9333038330078
to: long 43.92102813720703 lat -61.33552932739258


In [16]:
print("mean: long {} lat {}".format((data_frame.dropoff_latitude.mean()), (data_frame.dropoff_longitude.mean()))  )

mean: long 40.7517995149002 lat -73.9734159469458


In [17]:
def euklidian_dist(a_x,a_y,b_x,b_y):
    return np.sqrt((a_x - b_x)**2 + (a_y - b_y)**2)

def manhattan_dist(a_x,a_y,b_x,b_y):
    return np.absolute(a_x - b_x) + np.absolute(a_y - b_y)

Here we define our custom fields:
    1. Transform field pickup_datetime to extract information about: month, day of the month, day of the week 
        and hour.
        
    2. Euklidian distance between pickup place and dropoff place.
    
    3. Mahattan distance between pickup place and dropoff place, because we operate in NYC.
    
    4. We also transform trip_duration field with log function.

In [18]:
data_frame['datetime'] = pd.to_datetime(data_frame.pickup_datetime)
data_frame['day_of_week'] = data_frame.datetime.dt.dayofweek
data_frame['hour'] = data_frame.datetime.dt.hour
data_frame['day_of_month'] = data_frame.datetime.dt.day
data_frame['month'] = data_frame.datetime.dt.month
data_frame['euklidian_distance'] = euklidian_dist(data_frame.dropoff_latitude,  data_frame.dropoff_longitude, data_frame.pickup_latitude,data_frame.pickup_longitude)
data_frame['manhattan_distance'] = manhattan_dist(data_frame.dropoff_latitude,  data_frame.dropoff_longitude, data_frame.pickup_latitude,data_frame.pickup_longitude)
data_frame['log_trip_duration'] = np.log(data_frame.trip_duration)

In [19]:
#actual data frame
data_frame[:11]

id  vendor_id      pickup_datetime     dropoff_datetime  \
0   id2875421          2  2016-03-14 17:24:55  2016-03-14 17:32:30   
1   id2377394          1  2016-06-12 00:43:35  2016-06-12 00:54:38   
2   id3858529          2  2016-01-19 11:35:24  2016-01-19 12:10:48   
3   id3504673          2  2016-04-06 19:32:31  2016-04-06 19:39:40   
4   id2181028          2  2016-03-26 13:30:55  2016-03-26 13:38:10   
5   id0801584          2  2016-01-30 22:01:40  2016-01-30 22:09:03   
6   id1813257          1  2016-06-17 22:34:59  2016-06-17 22:40:40   
7   id1324603          2  2016-05-21 07:54:58  2016-05-21 08:20:49   
8   id1301050          1  2016-05-27 23:12:23  2016-05-27 23:16:38   
9   id0012891          2  2016-03-10 21:45:01  2016-03-10 22:05:26   
10  id1436371          2  2016-05-10 22:08:41  2016-05-10 22:29:55   

    passenger_count  pickup_longitude  pickup_latitude  dropoff_longitude  \
0                 1        -73.982155        40.767937         -73.964630   
1                 1        -73.980415        40.738564         -73.999481   
2                 1        -73.979027        40.763939         -74.005333   
3                 1        -74.010040        40.719971         -74.012268   
4                 1        -73.973053        40.793209         -73.972923   
5                 6        -73.982857        40.742195         -73.992081   
6                 4        -73.969017        40.757839         -73.957405   
7                 1        -73.969276        40.797779         -73.922470   
8                 1        -73.999481        40.738400         -73.985786   
9                 1        -73.981049        40.744339         -73.973000   
10                1        -73.982651        40.763840         -74.002228   

    dropoff_latitude store_and_fwd_flag  trip_duration            datetime  \
0          40.765602                  N            455 2016-03-14 17:24:55   
1          40.731152                  N            663 2016-06-12 00:43:35   
2          40.710087                  N           2124 2016-01-19 11:35:24   
3          40.706718                  N            429 2016-04-06 19:32:31   
4          40.782520                  N            435 2016-03-26 13:30:55   
5          40.749184                  N            443 2016-01-30 22:01:40   
6          40.765896                  N            341 2016-06-17 22:34:59   
7          40.760559                  N           1551 2016-05-21 07:54:58   
8          40.732815                  N            255 2016-05-27 23:12:23   
9          40.789989                  N           1225 2016-03-10 21:45:01   
10         40.732990                  N           1274 2016-05-10 22:08:41   

    day_of_week  hour  day_of_month  month  euklidian_distance  \
0             0    17            14      3            0.017680   
1             6     0            12      6            0.020456   
2             1    11            19      1            0.059934   
3             2    19             6      4            0.013438   
4             5    13            26      3            0.010690   
5             5    22            30      1            0.011572   
6             4    22            17      6            0.014133   
7             5     7            21      5            0.059801   
8             4    23            27      5            0.014790   
9             3    21            10      3            0.046355   
10            1    22            10      5            0.036537   

    manhattan_distance  log_trip_duration  
0             0.019859           6.120297  
1             0.026478           6.496775  
2             0.080158           7.661056  
3             0.015480           6.061457  
4             0.010818           6.075346  
5             0.016212           6.093570  
6             0.019669           5.831882  
7             0.084026           7.346655  
8             0.019279           5.541264  
9             0.053699           7.110696  
10            0.050426         

We tranform use log function on trip_duration, because it is supposed reduce skeewnes.

More on that here
https://becominghuman.ai/how-to-deal-with-skewed-dataset-in-machine-learning-afd2928011cc

All I know is that can help with regression in some cases, and it was true in ours.

Here is what is correlation between given fields and a trip_duration, it gives us information how each field influences the output:


And here is correlation betwen given fields and log_trip_duration:


We pick fields for later training. We have decided to use both euklidian and manhattan distance, because this configuration gave us the best results.

In [34]:
data_X   = data_frame[[
        'pickup_longitude', 'pickup_latitude',
        'dropoff_longitude', 'dropoff_latitude',
        'month', 'hour',
        'euklidian_distance',
        'manhattan_distance',
    
       ]].values



data_y = data_frame['log_trip_duration'].values

In [35]:

train_X, test_X, train_y, test_y = train_test_split(data_X, data_y, test_size=0.2)

In [36]:
train_X

array([[ -7.39649582e+01,   4.07725754e+01,  -7.39607239e+01, ...,
          1.80000000e+01,   7.31295375e-03,   1.01966858e-02],
       [ -7.39895401e+01,   4.07400093e+01,  -7.39935684e+01, ...,
          9.00000000e+00,   1.26409979e-02,   1.60102844e-02],
       [ -7.37900467e+01,   4.06469383e+01,  -7.39790802e+01, ...,
          1.50000000e+01,   2.21157954e-01,   3.03825378e-01],
       ..., 
       [ -7.39905090e+01,   4.07410583e+01,  -7.39750214e+01, ...,
          2.00000000e+01,   1.68727061e-02,   2.21824646e-02],
       [ -7.38638306e+01,   4.07697868e+01,  -7.40070496e+01, ...,
          1.70000000e+01,   1.46451808e-01,   1.73820496e-01],
       [ -7.39623795e+01,   4.07706490e+01,  -7.39758301e+01, ...,
          1.10000000e+01,   1.51577945e-02,   2.04391479e-02]])

We scale our input. By calculating mean of each column, and then dividing each element by mean of column it is in. After that operation all input fields should be moreover the same.

In [37]:
means = np.array([np.mean(train_X[:,i]) for i in range(len(train_X[0]))])
train_X = train_X / means
test_X = test_X / means
print(means)


[ -7.39734503e+01   4.07509192e+01  -7.39733898e+01   4.07517839e+01
   3.51708479e+00   1.36067434e+01   3.55015215e-02   4.59241450e-02]


# Production Model

**4 .Gradient Boosted Trees**

In [39]:
from sklearn.ensemble import GradientBoostingRegressor
from sklearn.ensemble import RandomForestRegressor
from sklearn.externals import joblib
from sklearn.metrics import mean_squared_error

In [14]:
n = 50000
model1 = GradientBoostingRegressor(criterion='mse')
%timeit model1.fit(train_X[:n],train_y[:n])
joblib.dump(model1,"models/production50k.pkl")
print("DONE")

4.88 s ± 329 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [15]:
n = 100000
model2 = GradientBoostingRegressor(criterion='mse')
%timeit model2.fit(train_X[:n],train_y[:n])
joblib.dump(model2,"models/production100k.pkl")
print("DONE")

13.5 s ± 663 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [16]:
n = 200000
model3 = GradientBoostingRegressor(criterion='mse')
%timeit model3.fit(train_X[:n],train_y[:n])
joblib.dump(model3,"models/production200k.pkl")
print("DONE")

29.9 s ± 383 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [17]:
n = 400000
model4 = GradientBoostingRegressor(criterion='mse')
%timeit model4.fit(train_X[:n],train_y[:n])
joblib.dump(model4,"models/production400k.pkl")
print("DONE")

1min 12s ± 1.9 s per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [27]:
model4 = GradientBoostingRegressor(criterion='mse')
%timeit model4.fit(train_X,train_y)
joblib.dump(model4,"models/production_full.pkl")
print("DONE")

3min 5s ± 9.64 s per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [40]:
model4 = joblib.load("models/production_full.pkl")
result = model4.predict(test_X)
print(mean_squared_error(test_y, result))

0.269155333597


In [84]:
result = model4.predict(test_X)
from sklearn.metrics import mean_absolute_error
print((mean_absolute_error((test_y), (result))))

2.21413597513
78.8577273677 1450.0
55.8697654024 263.0
76.8238331702 1077.0
166.457178276 1741.0
75.0852399406 963.0
68.9802000409 775.0
68.9802000409 595.0
83.7279983469 1722.0
76.8238331702 939.0
56.238352994 311.0
78.8577273677 1052.0
75.0852399406 893.0
109.696013101 1164.0
75.0852399406 710.0
75.0852399406 875.0
69.4352806309 912.0
50.2048645281 512.0
56.238352994 628.0
78.8577273677 866.0
75.0852399406 578.0
68.9802000409 313.0
56.238352994 684.0
75.0852399406 599.0
78.8577273677 1298.0
38.0532724361 1104.0
78.8577273677 716.0
59.8884249657 260.0
77.8619540665 834.0
76.8238331702 668.0
83.1792429225 1267.0
75.0852399406 1380.0
83.7279983469 1503.0
76.3203278195 1118.0
78.8577273677 1362.0
59.8884249657 702.0
78.3408918228 1179.0
50.5360792732 216.0
75.0852399406 240.0
78.8577273677 2003.0
91.0503656495 497.0
56.238352994 526.0
94.379902988 2023.0
69.4352806309 713.0
75.0852399406 639.0
95.6249845748 624.0
69.4352806309 458.0
59.8884249657 573.0
56.238352994 311.0
171.511474865 20

78.8577273677 790.0
50.5360792732 203.0
75.0852399406 577.0
69.4352806309 1019.0
89.8686000734 1284.0
83.7279983469 1001.0
83.7279983469 1376.0
74.593129374 441.0
83.7279983469 1167.0
75.0852399406 900.0
90.4614869528 2052.0
78.8577273677 549.0
99.9215260875 2048.0
75.0852399406 1104.0
76.3203278195 1076.0
46.7441020243 269.0
55.8697654024 292.0
78.3408918228 703.0
76.8238331702 1262.0
78.8577273677 671.0
56.238352994 726.0
82.6707258626 1658.0
37.8038703236 764.0
68.9802000409 491.0
69.4352806309 865.0
75.0852399406 557.0
59.8884249657 420.0
34.0574869156 187.0
78.8577273677 1370.0
78.8577273677 760.0
59.8884249657 306.0
78.8577273677 1184.0
59.8884249657 367.0
78.8577273677 415.0
74.593129374 1491.0
78.8577273677 1196.0
52.266623026 235.0
59.8884249657 393.0
69.4352806309 614.0
90.4792744319 2624.0
83.7279983469 1046.0
78.8577273677 948.0
75.0852399406 710.0
75.0852399406 778.0
83.7279983469 1387.0
78.8577273677 580.0
75.0852399406 343.0
59.8884249657 399.0
78.3408918228 717.0
69.435

56.238352994 414.0
78.8577273677 784.0
50.5360792732 338.0
69.4352806309 1008.0
76.8238331702 1439.0
69.4352806309 408.0
50.2048645281 116.0
83.7279983469 1360.0
56.238352994 420.0
75.0852399406 882.0
78.3408918228 859.0
78.8577273677 761.0
75.0852399406 479.0
75.0852399406 725.0
78.8577273677 1770.0
90.4614869528 2398.0
86.9898218379 1531.0
75.0852399406 1215.0
69.4352806309 321.0
83.7279983469 1079.0
56.238352994 580.0
86.9898218379 1645.0
78.8577273677 536.0
69.4352806309 291.0
56.238352994 461.0
56.238352994 157.0
69.4352806309 616.0
90.4614869528 1226.0
83.7279983469 1544.0
47.0524852055 466.0
78.3408918228 1140.0
74.593129374 1465.0
56.238352994 289.0
59.8884249657 350.0
56.238352994 402.0
68.9802000409 742.0
55.5282050823 432.0
76.8238331702 476.0
159.804748287 5266.0
74.593129374 787.0
59.8884249657 401.0
86.4196883397 2157.0
56.238352994 419.0
69.4352806309 450.0
83.7279983469 847.0
83.7279983469 1938.0
75.0852399406 979.0
56.238352994 501.0
78.8577273677 641.0
83.7279983469 8

56.1362528047 651.0
90.4614869528 2287.0
69.4352806309 728.0
69.4352806309 532.0
69.4352806309 308.0
68.9802000409 540.0
33.1592560562 101.0
59.8884249657 126.0
23.869986163 3.0
46.7441020243 561.0
34.0574869156 161.0
75.0852399406 554.0
83.1792429225 667.0
75.541146832 858.0
68.9802000409 455.0
75.0852399406 829.0
69.4352806309 458.0
69.4352806309 351.0
47.0524852055 500.0
75.0852399406 1120.0
75.0852399406 690.0
78.8577273677 1177.0
82.6707258626 1033.0
74.593129374 1340.0
83.7279983469 2695.0
177.534407874 3650.0
83.7279983469 1205.0
69.4352806309 220.0
59.8884249657 413.0
78.8577273677 1037.0
82.1163219872 266.0
74.593129374 556.0
68.9802000409 483.0
78.3408918228 1379.0
75.0852399406 680.0
56.238352994 519.0
83.7279983469 2203.0
83.7279983469 1636.0
83.7279983469 1464.0
78.3408918228 935.0
75.0852399406 1529.0
55.8697654024 450.0
74.593129374 493.0
75.0852399406 661.0
75.8537427996 697.0
86.9898218379 3500.0
68.9802000409 733.0
55.8697654024 120.0
78.3408918228 663.0
55.8697654024

59.8884249657 146.0
83.7279983469 1751.0
84.1990742178 596.0
78.8577273677 355.0
55.8697654024 481.0
94.3613486776 2237.0
78.8577273677 432.0
75.0852399406 518.0
50.5360792732 157.0
78.8577273677 818.0
75.0852399406 331.0
164.785101575 4121.0
83.1792429225 839.0
56.238352994 681.0
56.238352994 423.0
55.8697654024 170.0
59.8884249657 427.0
76.3203278195 1220.0
125.979564894 1591.0
50.5360792732 357.0
50.2048645281 146.0
75.0852399406 1019.0
78.8577273677 1644.0
78.8577273677 870.0
35.9191809085 329.0
56.238352994 237.0
69.4352806309 218.0
69.4352806309 568.0
69.4352806309 470.0
75.0852399406 1568.0
83.7279983469 718.0
83.7279983469 1014.0
101.53080513 1083.0
78.8577273677 740.0
59.8884249657 252.0
59.8884249657 345.0
56.1362528047 214.0
78.8577273677 818.0
74.593129374 1142.0
47.0524852055 492.0
69.4352806309 577.0
56.238352994 403.0
56.238352994 297.0
81.7870812872 741.0
55.8697654024 179.0
75.0852399406 474.0
83.1792429225 587.0
83.7279983469 1621.0
78.8577273677 781.0
75.0852399406 6

...

59.8884249657 325.0
69.4352806309 663.0
34.0574869156 602.0
83.7279983469 1545.0
56.238352994 78.0
56.238352994 788.0
75.0852399406 646.0
76.8238331702 854.0
38.1427568075 182.0
75.0852399406 1178.0
75.0852399406 639.0
32.9998275558 118.0
59.8884249657 605.0
59.8884249657 358.0
69.4352806309 265.0
75.0852399406 1124.0
76.8238331702 1438.0
78.8577273677 570.0
31.3235589639 2.0
55.5282050823 1064.0
76.8238331702 1089.0
50.5360792732 420.0
66.509225001 413.0
59.4959147097 308.0
56.238352994 969.0
83.1792429225 1131.0
90.4614869528 1580.0
59.8884249657 286.0
165.256992801 1329.0
75.0852399406 1276.0
28.0335723549 183.0
78.8577273677 1622.0
90.4614869528 2762.0
75.0852399406 503.0
50.5360792732 260.0
123.089412671 1901.0
76.8238331702 1141.0
83.7279983469 967.0
78.8577273677 946.0
56.238352994 571.0
75.0852399406 724.0
86.9898218379 1041.0
69.4352806309 434.0
59.8884249657 232.0
78.3408918228 1118.0
165.242286982 3473.0
87.4516675361 2676.0
75.0852399406 999.0
78.3408918228 1359.0
173.25180

56.1362528047 449.0
47.0524852055 473.0
75.0852399406 723.0
78.8577273677 1040.0
69.4352806309 608.0
87.4516675361 1690.0
78.8577273677 777.0
78.8577273677 566.0
69.4352806309 336.0
82.6707258626 1137.0
78.8577273677 1538.0
75.0852399406 689.0
68.9802000409 596.0
83.7279983469 1447.0
59.8884249657 206.0
47.0524852055 284.0
166.457178276 5047.0
56.238352994 333.0
56.1362528047 446.0
136.470662074 1586.0
78.8577273677 708.0
90.4614869528 1494.0
59.4959147097 276.0
75.0852399406 964.0
90.4614869528 1128.0
59.8884249657 265.0
56.238352994 467.0
105.315974586 1979.0
78.8577273677 1433.0
56.238352994 671.0
59.8884249657 503.0
76.8238331702 1190.0
75.0852399406 758.0
75.0852399406 550.0
76.3203278195 471.0
78.8577273677 1046.0
75.0852399406 580.0
76.8238331702 793.0
33.1592560562 143.0
83.7279983469 1164.0
75.0852399406 575.0
59.4959147097 226.0
56.238352994 649.0
83.7279983469 1702.0
172.637411656 1948.0
86.4196883397 1358.0
83.7279983469 707.0
69.4352806309 787.0
83.7279983469 1384.0
75.085

69.4352806309 756.0
59.4959147097 654.0
75.8537427996 1018.0
59.8884249657 556.0
76.3203278195 1407.0
56.238352994 515.0
78.8577273677 479.0
78.8577273677 1071.0
76.3203278195 1113.0
78.8577273677 596.0
69.4352806309 511.0
75.0852399406 760.0
78.8577273677 420.0
69.4352806309 616.0
69.4352806309 490.0
78.8577273677 1587.0
78.8577273677 1181.0
78.8577273677 1485.0
82.6707258626 2111.0
47.0524852055 226.0
47.0524852055 172.0
59.4959147097 482.0
75.0852399406 1363.0
78.3408918228 463.0
83.1792429225 1131.0
75.0852399406 859.0
55.8697654024 106.0
75.0852399406 659.0
211.242037312 3502.0
75.0852399406 846.0
75.0852399406 847.0
78.8577273677 946.0
76.8238331702 1405.0
83.7279983469 951.0
75.0852399406 360.0
69.4352806309 741.0
69.4352806309 542.0
95.6249845748 594.0
53.3834024862 127.0
50.5360792732 284.0
69.4352806309 707.0
83.7279983469 1946.0
56.238352994 275.0
69.4352806309 745.0
74.593129374 533.0
75.0852399406 565.0
86.4196883397 873.0
68.9802000409 427.0
55.8697654024 338.0
76.8238331

99.9411736979 2367.0
38.0532724361 168.0
78.8577273677 1109.0
59.8884249657 132.0
75.0852399406 535.0
69.4352806309 335.0
59.8884249657 218.0
33.1592560562 46.0
56.238352994 181.0
69.4352806309 432.0
75.0852399406 1045.0
83.7279983469 1859.0
75.0852399406 527.0
78.8577273677 993.0
59.8884249657 332.0
56.238352994 1174.0
164.785101575 2337.0
83.7279983469 1006.0
83.7279983469 1101.0
56.238352994 449.0
78.8577273677 511.0
69.4352806309 541.0
90.4614869528 1516.0
50.2048645281 277.0
77.0297091258 969.0
75.0852399406 798.0
75.0852399406 671.0
59.8884249657 207.0
69.4352806309 687.0
68.9802000409 411.0
46.6851920694 223.0
78.8577273677 669.0
59.8884249657 528.0
99.9215260875 1650.0
69.4352806309 439.0
75.0852399406 639.0
75.0852399406 713.0
56.238352994 977.0
78.8577273677 514.0
78.8577273677 1017.0
76.3203278195 670.0
78.8577273677 585.0
75.0852399406 85035.0
90.4614869528 1632.0
50.2048645281 300.0
69.4352806309 1443.0
83.7279983469 1216.0
83.1792429225 860.0
177.534407874 2126.0
78.85772

68.9802000409 487.0
69.4352806309 1467.0
78.8577273677 736.0
78.8577273677 923.0
59.8884249657 153.0
68.9802000409 374.0
69.4352806309 555.0
78.8577273677 667.0
56.238352994 335.0
59.8884249657 109.0
75.0852399406 766.0
59.8884249657 393.0
56.238352994 314.0
59.8884249657 258.0
165.758705957 1708.0
69.4352806309 1169.0
78.3408918228 918.0
59.4959147097 344.0
78.8577273677 584.0
69.4352806309 635.0
83.7279983469 748.0
78.3408918228 932.0
75.0852399406 571.0
23.869986163 75.0
76.8238331702 1145.0
75.0852399406 872.0
56.238352994 523.0
76.8238331702 1054.0
91.0503656495 462.0
83.7279983469 1397.0
56.238352994 262.0
75.0852399406 1257.0
84.1990742178 400.0
69.4352806309 363.0
59.4959147097 255.0
78.8577273677 685.0
78.3408918228 821.0
75.0852399406 1122.0
55.8697654024 481.0
33.8342732827 80.0
88.7981395542 753.0
83.7279983469 1806.0
78.8577273677 700.0
59.8884249657 874.0
75.0852399406 982.0
59.8884249657 372.0
69.4352806309 845.0
59.4959147097 122.0
78.8577273677 350.0
75.0852399406 539.

In [81]:
result = model3.predict(test_X)
from sklearn.metrics import mean_squared_error
print(mean_squared_error(test_y, result))

3.01588065319


In [127]:
result = model2.predict(test_X)

from sklearn.metrics import mean_squared_error
print(mean_squared_error(test_y, result))

NotFittedError: Estimator not fitted, call `fit` before exploiting the model.

In [128]:
result = model1.predict(test_X)


print(mean_squared_error(test_y, result))

ValueError: Number of features of the model must match the input. Model n_features is 8 and input n_features is 14 

In [70]:
n = 50000
model1 = GradientBoostingRegressor(criterion='mse')
%timeit model1.fit(train_X[:n],train_y[:n])

print("DONE")

2.9 s ± 75.7 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [75]:
result = model1.predict(test_X)
from sklearn.metrics import mean_squared_error
print(mean_squared_error(test_y, result))

9.8473877904


In [90]:
#RF

In [91]:
n = 100000
model2 = RandomForestRegressor(criterion='mse')
%timeit model2.fit(train_X[:n],train_y[:n])
joblib.dump(model2,"models/rf100k.pkl")
print("DONE")

6.89 s ± 59.4 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
DONE


In [92]:
result = model2.predict(test_X)

from sklearn.metrics import mean_squared_error
print(mean_squared_error(test_y, result))

3.16632234161


In [125]:
#test model
n = 100000
test_model = RandomForestRegressor(criterion='mse')
%timeit test_model.fit(train_X[:n],train_y[:n])
joblib.dump(test_model,"models/test_model.pkl")

7.59 s ± 189 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


['test_model.pkl']

In [126]:
result = (test_model.predict(test_X))
test = (test_y)
from sklearn.metrics import mean_squared_error
print(np.sqrt(mean_squared_error(test, result)))

0.453649930883


In [119]:
for i, a in enumerate(result[:10]):
    print(np.exp(a), np.exp(test_y[i]))

92.8834267702 54.0
315.824570376 238.0
277.795349954 302.0
645.006425836 802.0
1330.05628379 1299.0
544.287833484 591.0
282.884428681 116.0
426.10938765 187.0
1309.4945752 1238.0
2180.17113919 2089.0


In [122]:
#test gb
#test model
n = 100000
test_model = GradientBoostingRegressor(criterion='mse')
%timeit test_model.fit(train_X[:n],train_y[:n])

12.8 s ± 992 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)


In [124]:
result =(test_model.predict(test_X))
test = (test_y)
from sklearn.metrics import mean_squared_error
print(np.sqrt(mean_squared_error(test, result)))

0.449382060985


In [129]:
data_X   = data_frame[[
        'pickup_longitude', 'pickup_latitude',
        'dropoff_longitude', 'dropoff_latitude',
        'hour', 'month','euklidian_distance',
        'manhattan_distance',
       ]].values

train_X, test_X, train_y, test_y = train_test_split(data_X, data_y, test_size=0.2)

means = np.array([np.mean(train_X[:,i]) for i in range(len(train_X[0]))])
train_X = train_X / means
test_X = test_X / means

n = 100000
test_model = GradientBoostingRegressor(criterion='mse')
%timeit test_model.fit(train_X[:n],train_y[:n])

result =(test_model.predict(test_X))
test = (test_y)
from sklearn.metrics import mean_squared_error
print(np.sqrt(mean_squared_error(test, result)))

9.89 s ± 618 ms per loop (mean ± std. dev. of 7 runs, 1 loop each)
0.454043893435
